# LOC Colors - Data Management

*Export data as minimal JSON files - only the essentials to create the swatches in the browser*

To use the created swatches for [https://labs.onb.ac.at/en/topic/akon-swatches/](https://labs.onb.ac.at/en/topic/akon-swatches/), I have to create a JSON file looking like this:

```json
[["AK111_461", ["#f4e6cd", "#cac4b2", "#7e8077", "#3e4139", "#2f3431", "#000304"], "Nonza", "gelaufen 1903"],
["AK111_072", ["#e2d7c1", "#a19c8f", "#504e42", "#494a44", "#010500", "#393c39"], "Kirchberg am Walde", "gelaufen 1914"],
["AK111_077", ["#454234", "#3e3b1f", "#7f7e77", "#a9b8be", "#3b4347", "#425a6b"], "Kirchberg am Wechsel", "gelaufen 1913"]]
```

The first part (the id and the colors) are part of the created swatches, the second part (a name and an approximate date) are part of the metadata to download here: [https://labs.onb.ac.at/gitlab/labs-team/raw-metadata/raw/master/akon_postcards_public_domain.csv.bz2?inline=false](https://labs.onb.ac.at/gitlab/labs-team/raw-metadata/raw/master/akon_postcards_public_domain.csv.bz2?inline=false).

### Read created swatches

In [1]:
import pandas as pd

In [2]:
df = pd.read_csv('historic_postcards_color_swatches.csv.bz2', compression='bz2')

In [3]:
df.sample()

Unnamed: 0    akon_id  \
21914       21914  AK036_405   

                                              image_link  \
21914  https://iiif.onb.ac.at/images/AKON/AK036_405/4...   

                                              hex_colors  \
21914  ['#f2e3c1', '#e6dec6', '#8e8a7a', '#7b7864', '...   

                                                    html  
21914  <a href="https://iiif.onb.ac.at/images/AKON/AK...

Only keep the necessary columns

In [4]:
id_and_hex_colors = df[['akon_id', 'hex_colors']].copy()

In [5]:
id_and_hex_colors.sample(5)

akon_id                                         hex_colors
14980  AK010_595  ['#cfbfa4', '#62583b', '#c8c7b6', '#4f5144', '...
7474   AK084_243  ['#aca693', '#414028', '#444537', '#5c5f57', '...
23730  AK043_578  ['#4e502c', '#444735', '#51554a', '#dae1d1', '...
30352  AK085_096  ['#b5aa9d', '#f3e7d7', '#756d62', '#211a0f', '...
22389  AK038_067  ['#f2e9cb', '#989384', '#545245', '#fcf7db', '...

### Parse Color Array

In order to properly export the color array as a JSON array later, convert the data representation slightly.

In [6]:
import json

In [7]:
id_and_hex_colors['colors'] = id_and_hex_colors['hex_colors'].apply(
    lambda c: json.loads(c.replace("'", '"'))
)

In [8]:
id_and_hex_colors.sample()

akon_id                                         hex_colors  \
1291  AK116_455  ['#f4ece0', '#d4d2ce', '#716d5c', '#65665e', '...   

                                                 colors  
1291  [#f4ece0, #d4d2ce, #716d5c, #65665e, #b2b4bb, ...

Do you see the subtle difference? The entry in the colors column is now an array with strings _without_ the single quotes `'`.

In [9]:
id_and_colors = id_and_hex_colors[['akon_id', 'colors']].copy()

## Add Metadata From Original Records

Next up: Combining the id and the color array with names and dates. Read the metadata dump directly from the link found on [https://labs.onb.ac.at/en/dataset/akon/](https://labs.onb.ac.at/en/dataset/akon/):

In [10]:
original = pd.read_csv('https://labs.onb.ac.at/gitlab/labs-team/raw-metadata/raw/master/akon_postcards_public_domain.csv.bz2?inline=false', compression='bz2')

/opt/conda/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (13) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


In [11]:
original[['akon_id', 'name', 'date']].sample(10)

akon_id               name           date
16251  AK016_087        Neulengbach       vor 1907
23864  AK044_401          Gloriette           1907
33292  AK085_517             Milano       vor 1905
13875  AK008_070  Schloß Schönbrunn           1906
12223  AK004_040              Pürgg           1909
4129   AK125_097          Altaussee  gelaufen 1901
23756  AK044_080  Radstädter Tauern           1907
26479  AK069_067           Attersee           1906
14251  AK109_329         Josefsthal       vor 1907
28518  AK063_083             Gaußig           1908

These are the columns needed.

In [12]:
original_info = original[['akon_id', 'name', 'date']].copy()

In [13]:
original_info.sample(2)

akon_id                  name      date
24871  AK048_377  Reichenau an der Rax      1925
4191   AK054_543         Aflenz Kurort  vor 1905

Pandas offers a handy function for merging two dataframes _not on the index_, but on a shared column:

In [15]:
colors_and_info = pd.merge(id_and_colors, original_info, on='akon_id')

In [16]:
colors_and_info.sample(2)

akon_id                                             colors      name  \
16356  AK016_310  [#5f5a57, #9c938c, #4d453f, #cabbab, #3c3b39, ...  Kapellen   
1117   AK116_129  [#dcc9ab, #cec0a7, #a8a290, #48473a, #6c6c62, ...   Garsten   

                date  
16356           1908  
1117   gelaufen 1902

That's exactly what's needed.

## Save to JSON-File

Pandas can export the data exactly in the target format:

In [17]:
colors_and_info.to_json('historic_postcards__id_colors_name_date.json', orient='values')

## Extract Subset

That's almost all. For the preview on [https://labs.onb.ac.at/en/dataset/akon/](https://labs.onb.ac.at/en/dataset/akon/) I need a subset of 100 swatches and save them:

In [18]:
id_and_colors_100 = colors_and_info.iloc[:100]

In [19]:
id_and_colors_100.sample(5)

akon_id                                             colors  \
99  AK111_207  [#403e2c, #f9f8eb, #7e7f6b, #35362d, #32342f, ...   
34  AK111_293  [#e6d8bf, #c7c1b1, #4a4c3c, #aeafa5, #464740, ...   
86  AK111_184  [#f7edd6, #d1cbb8, #f6f0db, #2d2a1b, #9e9f93, ...   
3   AK111_026  [#e2cba6, #9e8e73, #574c39, #3c311a, #4c473b, ...   
39  AK111_072  [#e5d9c2, #c0baac, #928e81, #4c493e, #484943, ...   

                  name           date  
99      Klosterneuburg  gelaufen 1908  
34             Komotau       vor 1905  
86         Klausenburg  gelaufen 1904  
3             Kierling           1922  
39  Kirchberg am Walde  gelaufen 1914

In [20]:
id_and_colors_100.to_json('historic_postcards__id_colors_name_date__100.json', orient='values')

And done!

Below there's a fast-forward, compact version of what's been done above. No need to do all this again.

# Compact (with other data source)

## Load Data

In [65]:
colors_hsv_clip = pd.read_csv('akon_with_hsv_clip50_color_swatches.csv.bz2', compression='bz2')
raw_data = pd.read_csv('akon_postcards_public_domain_1925.csv.bz2', compression='bz2')

/opt/conda/lib/python3.6/site-packages/IPython/core/interactiveshell.py:2785: DtypeWarning: Columns (13) have mixed types. Specify dtype option on import or set low_memory=False.
  interactivity=interactivity, compiler=compiler, result=result)


## View Data Format

In [66]:
colors_hsv_clip.sample()

Unnamed: 0    akon_id  \
11914       11914  AK003_285   

                                              image_link  \
11914  https://iiif.onb.ac.at/images/AKON/AK003_285/2...   

                                              hex_colors  \
11914  ['#050300', '#eee2c9', '#b6af9e', '#fdf7da', '...   

                                                    html  
11914  <a href="https://iiif.onb.ac.at/images/AKON/AK...

In [67]:
raw_data.sample()

Unnamed: 0    akon_id     id  altitude building         city  color  \
23435       23435  AK042_533  25265     434.0      NaN  Frohnleiten  False   

      comment mountain other         ...         feature_class feature_code  \
23435     NaN      NaN   NaN         ...                     P        PPLA3   

      geoname_id  latitude longitude         name country_id admin_name_1  \
23435  2779202.0  47.26667  15.31667  Frohnleiten         AT          NaN   

      admin_code_1                 geo  
23435          NaN  47.26667, 15.31667  

[1 rows x 30 columns]

## Combine Data

In [68]:
combined_data = pd.merge(colors_hsv_clip[['akon_id', 'hex_colors', 'image_link']],
                         raw_data[['akon_id', 'name', 'date']],
                         on='akon_id')

In [69]:
combined_data.sample()

akon_id                                         hex_colors  \
23217  AK041_595  ['#ada896', '#fcf6d5', '#767467', '#484739', '...   

                                              image_link     name  date  
23217  https://iiif.onb.ac.at/images/AKON/AK041_595/5...  Ötscher  1909

## Flatten hex_colors

In [70]:
combined_data['hex_colors_list'] = combined_data['hex_colors'].apply(lambda c: json.loads(c.replace("'", '"')))

In [71]:
combined_data.sample()

akon_id                                         hex_colors  \
15996  AK014_589  ['#020100', '#fbfae8', '#88887e', '#64645a', '...   

                                              image_link          name  date  \
15996  https://iiif.onb.ac.at/images/AKON/AK014_589/5...  Maria Taferl  1909   

                                         hex_colors_list  
15996  [#020100, #fbfae8, #88887e, #64645a, #4d4f49, ...

## Sanitize and Reorder

In [73]:
combined_data = combined_data.drop(columns=['hex_colors']).copy()

In [74]:
combined_data.sample()

akon_id                                         image_link  \
19590  AK028_177  https://iiif.onb.ac.at/images/AKON/AK028_177/1...   

              name  date                                    hex_colors_list  
19590  Frohnleiten  1906  [#020100, #a8a599, #7b7a6f, #fbf9e5, #4b4b40, ...

In [78]:
combined_data = combined_data.rename(columns={'hex_colors_list': 'hex_colors'})

In [79]:
combined_data.sample()

akon_id                                         image_link     name  \
33304  AK087_042  https://iiif.onb.ac.at/images/AKON/AK087_042/0...  Abcoude   

           date                                         hex_colors  
33304  vor 1905  [#f8eacd, #aca391, #5b5747, #6e6a5e, #525148, ...

In [81]:
combined_data = combined_data[['akon_id', 'hex_colors', 'image_link', 'name', 'date']]
combined_data.sample()

akon_id                                         hex_colors  \
25575  AK031_287  [#444626, #caccbc, #4a4d41, #48504f, #5b7073, ...   

                                              image_link     name  date  
25575  https://iiif.onb.ac.at/images/AKON/AK031_287/2...  Ebensee  1907

## Sample and Write

In [82]:
combined_data.iloc[:100].to_json('swatches_100.json', orient='values')

In [83]:
combined_data.to_json('swatches_all.json', orient='values')

## Alternate Data Format Without Link

In [84]:
sans_link = combined_data[['akon_id', 'hex_colors', 'name', 'date']]

In [85]:
sans_link.iloc[:100].to_json('swatches_100_nolink.json', orient='values')

In [86]:
sans_link.to_json('swatches_all_nolink.json', orient='values')